In [3]:
import pandas as pd
import csv

In [ ]:
# # 댓글 데이터들의 전처리 과정입니다. 전처리된 파일로 대체합니다.

# data1 = pd.read_csv('badwords/reply_data1.csv', sep='\t')

# data1 = data1.replace(0, 2)
# data1 = data1.replace(1, 0)
# data1 = data1.replace(2, 1)

# data1 = data1.rename(columns={'content':'comment'})

# data1[data1['lable'].isnull()]
# data1['lable'] = pd.to_numeric(data1['lable'], errors='coerce')
# data1 = data1.dropna(subset=['lable'])
# data1['lable'] = data1['lable'].astype(int)

# f = open('badwords/reply_data2.txt', 'r', encoding='UTF-8')

# data2_list = f.read()

# f.close()

# data2_list = ''.join(data2_list.split('|'))
# data2_list = data2_list.split('\n')

# lable = []
# for i in range(0, len(data2_list)):
#     lable.append(data2_list[i][-1])
#     data2_list[i] = data2_list[i][:-1]

# data2 = pd.DataFrame([x for x in zip(data2_list,lable)])

# data2.columns = ['comment', 'lable']

# data3 = pd.read_csv('badwords/reply_data3.txt', sep = "\t", engine='python', encoding = "utf-8")
# data3 = data3.drop(['id'], axis=1)

# data3 = data3.replace(1, 2)
# data3 = data3.replace(0, 1)
# data3 = data3.replace(2, 0)

# data3.columns = ['comment', 'lable']

# data4 = pd.read_csv('badwords/reply_data4.tsv', sep = "\t", engine='python', encoding = "utf-8")

# data4 = data4.drop(['contain_gender_bias', 'bias'], axis=1)
# data4 = data4.replace('hate', 1)
# data4 = data4.replace('none', 0)

# data4.columns = ['comment', 'lable']

# reply_data = pd.concat([data1, data2, data4])
# data3 = data3.sample(n=40000)

# reply_data = pd.concat([reply_data, data3])
# reply_data

# reply_data = reply_data.replace('offensive', 1)
# reply_data['lable'] = reply_data['lable'].astype(int)

In [4]:
# 욕설 데이터 불러오기
f = open('badwords/badwords_data.txt', 'r', encoding = "utf-8")
bad_words = []

lines = f.readlines()
for line in lines:
    line = line.strip()
    if not line: break
    bad_words.append(line)
f.close()

In [6]:
import warnings
warnings.filterwarnings(action = 'ignore')
from konlpy.tag import Okt # 형태소 분석에 사용할 konlpy 패키지의 Okt 클래스를 임포트하고 okt 객체를 생성
okt = Okt()

# 레이블이 달린 댓글 데이터
train_df = pd.read_csv('badwords/reply_data.csv', engine='python', encoding = "utf-8")

# 댓글이 있는 항목만 담기(빈 댓글 삭제)
# text 컬럼이 non-null인 샘플만 train_df에 다시 저장
train_df = train_df[train_df['comment'].notnull()]

# 수정된 train_df의 정보를 다시 확인
print(train_df.info())

# 분류 클래스의 구성을 확인
print(train_df['lable'].value_counts())

<class 'pandas.core.frame.DataFrame'>
Int64Index: 63639 entries, 0 to 63638
Data columns (total 2 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   comment  63639 non-null  object
 1   lable    63639 non-null  int64 
dtypes: int64(1), object(1)
memory usage: 1.5+ MB
None
0    32189
1    31450
Name: lable, dtype: int64


In [7]:
# 한글 외 문자 제거(옵션)
import re # 정규식을 사용하기 위해 re 모듈을 임포트
# ‘ㄱ ~‘힣’까지의 문자를 제외한 나머지는 공백으로 치환, 영문: a-z| A-Z
train_df['comment'] = train_df['comment'].apply(lambda x : re.sub(r'[^ ㄱ-ㅣ가-힣]+', " ", x))
print(train_df.head())

# Train용 데이터셋의 정보를 재확인
print(train_df.info())
text = train_df['comment'] # 시리즈 객체로 저장
score = train_df['lable']

                                             comment  lable
0  이종석 한효주 나오는 드라마 이후로 드라마 안봤다   년전인가  좀 신선했었지  근...      1
1                       씨바알 노무노무 술프노  오늘 저녁은 꽂등심이다ㅠㅜ      1
2                                           짱깨 꺼라ㅡ패쓰      1
3  그들의 사생활   고인이된 설리를 위해서라도 모두 조용하길 지금 누굴 탓한다고 무슨...      0
4  아무리 법이 뭣같아도 무슨 자격으로 개인의 신상정보를 불특정 다수에게 공개하는지 도...      0
<class 'pandas.core.frame.DataFrame'>
Int64Index: 63639 entries, 0 to 63638
Data columns (total 2 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   comment  63639 non-null  object
 1   lable    63639 non-null  int64 
dtypes: int64(1), object(1)
memory usage: 1.5+ MB
None


In [8]:
from sklearn.model_selection import train_test_split
train_x, test_x, train_y, test_y = train_test_split(text, score , test_size=0.2, random_state=0)
print(len(train_x), len(train_y), len(test_x), len(test_y))

50911 50911 12728 12728


In [9]:
# 3분 정도 소요됩니다.
from sklearn.feature_extraction.text import TfidfVectorizer
tfv = TfidfVectorizer(tokenizer=okt.morphs, ngram_range=(1,2), min_df=3, max_df=0.9)
tfv.fit(train_x)
tfv_train_x = tfv.transform(train_x)
print(tfv_train_x)

  (0, 48825)	0.23451936642188656
  (0, 46363)	0.3052008882481903
  (0, 43746)	0.26797124466444283
  (0, 42286)	0.3273868526698094
  (0, 36575)	0.2094751846398965
  (0, 20966)	0.2785414821564677
  (0, 20781)	0.31661719035291097
  (0, 20730)	0.32155118070031913
  (0, 13543)	0.3273868526698094
  (0, 13542)	0.3273868526698094
  (0, 9515)	0.16189216817322188
  (0, 3513)	0.3273868526698094
  (1, 22239)	0.47574259688421255
  (1, 16600)	0.5770421588673107
  (1, 16585)	0.36055733592574674
  (1, 8450)	0.3921516959963592
  (1, 3023)	0.3961146087143547
  (2, 49932)	0.15711202293662382
  (2, 47660)	0.1505009485631296
  (2, 47300)	0.16250451843648028
  (2, 45121)	0.19803138487416605
  (2, 39755)	0.24102564392519896
  (2, 39753)	0.17917711954375098
  (2, 38262)	0.186300162022295
  (2, 35716)	0.21513759500186883
  :	:
  (50909, 7555)	0.2318632009621833
  (50909, 5156)	0.22275875656930685
  (50909, 1584)	0.18415947004925967
  (50909, 366)	0.17978352472785758
  (50910, 48995)	0.22353493991070425
  (5091

In [10]:
from sklearn.linear_model import LogisticRegression # 이진 분류 알고리즘
from sklearn.model_selection import GridSearchCV # 하이퍼 파라미터 최적화

clf = LogisticRegression(random_state=0)
params = {'C': [15, 18, 19, 20, 22]}
grid_cv = GridSearchCV(clf, param_grid=params, cv=3, scoring='accuracy', verbose=1)
grid_cv.fit(tfv_train_x, train_y)

# 최적의 평가 파라미터는 grid_cv.best_estimator_에 저장됨
print(grid_cv.best_params_, grid_cv.best_score_)# 가장 적합한 파라메터, 최고 정확도 확인

Fitting 3 folds for each of 5 candidates, totalling 15 fits
{'C': 15} 0.8018305760386353


In [85]:
tfv_test_x = tfv.transform(test_x)
# test_predict = grid_cv.best_estimator_.score(tfv_test_x,test_y)
test_predict = grid_cv.best_estimator_.predict(tfv_test_x)
from sklearn.metrics import accuracy_score
print('혐오 표현 분석 모델의 정확도 : ',round(accuracy_score(test_y, test_predict), 3))

혐오 표현 분석 모델의 정확도 :  0.822


In [88]:
input_text = '최인열은 쓰레기같고 인간 말종이다.'

#입력 텍스트에 대한 전처리 수행
input_text = re.compile(r'[ㄱ-ㅣ가-힣]+').findall(input_text)
input_text = [" ".join(input_text)]

# 입력 텍스트의 피처 벡터화
st_tfidf = tfv.transform(input_text)

# 최적 혐오표현 분석 모델에 적용하여 혐오표현 평가
st_predict = grid_cv.best_estimator_.predict(st_tfidf)

#예측 결과 출력
if(st_predict == 1):
    print("혐오표현")
else:
    print("혐오표현이 아님")

혐오표현


In [89]:
# 분석할 타겟 데이터 불러오기
taxi = pd.read_excel('data/hanmunchul_taxi.xlsx')

In [90]:
hate = 0
error = 0
hate_data = []

for i in range(0, len(taxi)):
    try:
        if (i % 500 == 0):
            print(input_text, st_tfidf)
        input_text = taxi['comment'][i]

        #입력 텍스트에 대한 전처리 수행
        input_text = re.compile(r'[ㄱ-ㅣ가-힣]+').findall(str(input_text))
        input_text = [" ".join(input_text)]

        # 입력 텍스트의 피처 벡터화
        st_tfidf = tfv.transform(input_text)

        # 최적 혐오표현 모델에 적용하여 혐오표현 평가
        st_predict = grid_cv.best_estimator_.predict(st_tfidf)

        #예측 결과 출력
        if(st_predict == 1):
            if (i % 500 == 0):
                hate_data.append(input_text)
            hate += 1
        else:
            continue
    except:
        error += 1
        pass

['최인열은 쓰레기같고 인간 말종이다']   (0, 41562)	0.41347862641245386
  (0, 37358)	0.4819417438708469
  (0, 37352)	0.2729371543327542
  (0, 25486)	0.242318422762036
  (0, 15677)	0.5013931398358504
  (0, 15627)	0.21456778269170232
  (0, 9621)	0.17748018063252877
  (0, 1921)	0.3669074055243554
혐오 표현 :  ['너도 꼭 이만큼만 당해라 나쁜시키']
혐오 표현 :  ['우리나라는 나쁜놈들이 잘사는나라예요 ㅡ오죽하면 돈에눈이뒤집어져가지고 응급환자를태운차를 가로막는 택시기사놈이 있겠어요 저는 잘못없으니 사람이죽어도 괜찮다는 사고방식이 싹텄겠어요 그래 택시기사같으놈들아 너희들은 꼭 그 배 배 고통받을테니 내가 그법을안다 이놈들아 이 멍청놈탴시기사같놈들아 법이 있던없든 한치에 오차도없이 지은대로 받는다는것을 기억하라 인과응보는자업자득 이것 꼭 기억해라 혼자 몰래 짖는죄 꼭 벌받는다 임마 배 배 배 곹 ㄷㅇ 받는다']
혐오 표현 :  ['저런 택시 족쳐야 된다 인간미가 없다 정말 쓰래기다 인간쓰래기']
혐오 표현 :  ['죽으면 지가 어떻게 책임 진다는거지 할복이라도 할건가 신상공개 됐으면 좋겠다']
혐오 표현 :  ['택시기사 이사람 사람이라고 해야합니까 사람아닙니다 발암물질 정도밖에는 암적인존재 으휴']
혐오 표현 :  ['사설이라도 거기에 환자가 있는지 없는지 응급한지 안한지 본인이 의사인가 겉은 말짱해도 응급환자 많은데 본인이 의사도 아니면서 장난하나 환자 사진찍은거면 그거 명예회손 될꺼같은데ㅡㅡ 길거리에서 도로에서 그 응급차 뒷차 오픈해서 사진찍은것도 문제고 근데 문제는 고인이 되셨으니 책임 져야겠네 저도 의도치 않게 사설 를 탔는데요 연락해도 사설이 더 빨리와요 책임지는거 어떻게 하시려는지ㅋㅋㅋㅋ 살인마']
혐오 표현 :  ['저 살인마놈 신상공개 급하다 가

In [91]:
# 욕설이 포함된 댓글 비율 분석
bad_words_count = 0

for i in range(0, len(taxi)):
    input_text = taxi['comment'][i]

    #입력 텍스트에 대한 전처리 수행
    input_text = re.compile(r'[ㄱ-ㅣ가-힣]+').findall(str(input_text))
    input_text = [" ".join(input_text)]

    if(any(bad_word in str(input_text) for bad_word in bad_words)):
        print(input_text)
        bad_words_count += 1

['우리나라는 나쁜놈들이 잘사는나라예요 ㅡ오죽하면 돈에눈이뒤집어져가지고 응급환자를태운차를 가로막는 택시기사놈이 있겠어요 저는 잘못없으니 사람이죽어도 괜찮다는 사고방식이 싹텄겠어요 그래 택시기사같으놈들아 너희들은 꼭 그 배 배 고통받을테니 내가 그법을안다 이놈들아 이 멍청놈탴시기사같놈들아 법이 있던없든 한치에 오차도없이 지은대로 받는다는것을 기억하라 인과응보는자업자득 이것 꼭 기억해라 혼자 몰래 짖는죄 꼭 벌받는다 임마 배 배 배 곹 ㄷㅇ 받는다']
['아니 영상 제일 앞에 블랙박스 원본 영상을 보여주고 시작하라니까 편집 진짜 개지랄같이 하네 정말']
['아우 진짜 저 쌍놈은 지금 봐도 화가나네']
['와 택시기사 ㅁㅊ네 저건 책임진다는대 책임안주면 너 나중에 지옥간다 그리고 지옥에서 용함애 빠진다']
['와진짜미친놈이네']
['살인자네 고의로 죽였구만 ㅁㅊㄸㄹ이']
['저런택시기사 ㅆㅂ세끼네 진짜 아우보는내가 화가 치밀어 오르네']
['년 개월형 살고 대한민국에서 꺼져라 알겠냐']
['전문가도 아니면서 저 상황을 본인이 판단하고 사람의 생명을 저렇게 쉽게 책임을 질 수 있다고 말하는 것이 말이 되나 니가 먼데 책임진다카노 ㅋㅋ 택시 기사 닌 진짜 미친놈이다 돌아가신 분이 택시 기사 니 때문인지 아닌지 알 수 없지만 기사 닌 누군가의 부모님이 치료받을 수 있는 정말 아까운 시간을 날려버린 놈이다 하 사람맞나 니도 누군가의 자식이잖아 누군가의 소중한 부모님 동생 누나 친구 형이 구급차로 이동 중이잖아 도대체 왜어ㅐ왜왜왜어애어ㅑ']
['재좀죽여주실분없나요 화가 존나치민다 진짜택시 개샡기']
['이 택레기 쉐끼 어찌 됐나요']
['최대한 고통스럽게 갔으면 좋겠다 미친놈이']
['죽으면 책임 죽으면 돌아 올 수가 없는데 지가 무슨 수로 책임을 지는데 법으로 구급차 고의적으로 막아서서 막장 부리는 놈들 차로 밀어버리든가 아구창 해머로 쳐서 기절시켜도 가능하게 해라']
['와 내가 저 상황이면 응급차에서 내려서 택시 운전사 끌어 내리고 생 지랄 했을텐데 택시운전사 미친넘'

In [92]:
print("욕설이 포함된 댓글 : ", round(bad_words_count / len(taxi) * 100, 3), "%")
print("모델이 혐오 표현으로 분류한 댓글 : ", round(hate / len(taxi) * 100, 3), "%")

욕설이 포함된 댓글 :  9.645 %
모델이 혐오 표현으로 분류한 댓글 :  41.008 %


In [11]:
import glob
import os

path = glob.glob('data/*')
data = []
for i in range(0, len(path)):
    data.append(os.path.basename(path[i]))

reply_result = pd.DataFrame({"Video" : data, 'bad_words': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0], 'hate': [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]})

In [12]:
error = 0
hate_data = []

for i in range(0, len(data)):
    hate = 0
    bad_words_count = 0
    reply = pd.read_excel('data/{}'.format(data[i]))

    for j in range(0, len(reply)):
        try:
            input_text = reply['comment'][j]

            #입력 텍스트에 대한 전처리 수행
            input_text = re.compile(r'[ㄱ-ㅣ가-힣]+').findall(str(input_text))
            input_text = [" ".join(input_text)]

            if(any(bad_word in str(input_text) for bad_word in bad_words)):
              bad_words_count += 1

            # 입력 텍스트의 피처 벡터화
            st_tfidf = tfv.transform(input_text)

            # 최적 혐오표현 모델에 적용하여 혐오표현 평가
            st_predict = grid_cv.best_estimator_.predict(st_tfidf)

            #예측 결과 출력
            if(st_predict == 1):
              hate_data.append(input_text)
              hate += 1
            else:
              continue
        except:
           error += 1
           pass

    reply_result.loc[i, 'bad_words'] = round(bad_words_count / len(reply) * 100, 3)
    reply_result.loc[i, 'hate'] = round(hate / len(reply) * 100, 3)
    hate_data.append("====" + data[i] + "====")
    print(reply_result)

                                              Video  bad_words  hate
0                             Cr-9RqDFy8s_쇼메이커.xlsx      5.833  37.5
1                              hanmunchul_benz.xlsx      0.000   0.0
2                              hanmunchul_bike.xlsx      0.000   0.0
3                              hanmunchul_taxi.xlsx      0.000   0.0
4                 JPtAxtvGKDo_여성할당제 토론하다 싸움날 뻔.xlsx      0.000   0.0
5                        LCK 결승전 T1 VS 담원 set2.xlsx      0.000   0.0
6                       LCK 결승전 T1 VS 담원 set4 .xlsx      0.000   0.0
7                                 man_vs_woman.xlsx      0.000   0.0
8                                      son_bad.xlsx      0.000   0.0
9                              TCzueqtnQUE_페이커.xlsx      0.000   0.0
10  xJIBg83BbF4_말도 안되는 갤럭시 S21 울트라 VS 3년 쓴 아이폰.xlsx      0.000   0.0
                                              Video  bad_words    hate
0                             Cr-9RqDFy8s_쇼메이커.xlsx      5.833  37.500
1                             

In [13]:
reply_result

Video  bad_words    hate
0                             Cr-9RqDFy8s_쇼메이커.xlsx      5.833  37.500
1                              hanmunchul_benz.xlsx     11.668  50.211
2                              hanmunchul_bike.xlsx      7.412  46.168
3                              hanmunchul_taxi.xlsx      9.645  41.008
4                 JPtAxtvGKDo_여성할당제 토론하다 싸움날 뻔.xlsx     14.950  62.125
5                        LCK 결승전 T1 VS 담원 set2.xlsx      6.497  45.244
6                       LCK 결승전 T1 VS 담원 set4 .xlsx      5.944  39.759
7                                 man_vs_woman.xlsx      8.326  50.042
8                                      son_bad.xlsx      4.454  28.161
9                              TCzueqtnQUE_페이커.xlsx      8.051  45.763
10  xJIBg83BbF4_말도 안되는 갤럭시 S21 울트라 VS 3년 쓴 아이폰.xlsx      9.499  37.995

In [27]:
hate_text = open('hate_text', 'w', encoding='UTF-8')

for i in range(0, len(hate_data)):
    input_text = re.compile(r'[ㄱ-ㅣ가-힣]+').findall(str(hate_data[i]))
    input_text = [" ".join(input_text)]
    hate_text.write(input_text[0] + "\n")

hate_text.close()